# Frame likelihood

In [46]:
using BSON: @save, @load
using Statistics
using DelimitedFiles
using Printf
using MDToolbox
using StatsBase 
using LinearAlgebra
using Random
using Plots

include("../src/afm.jl")

baumwelch (generic function with 1 method)

In [47]:
nq = 576
qs = readdlm("../data/quaternion/QUATERNION_LIST_$(nq)_Orient")
models = load_model("../data/t1r/cluster.pdb");
nmodel = size(models, 1)

test_radius = 25
pred_radii = [15, 18, 20, 25, 30, 32, 35]
sigma_noise = 3
sharpness = 10
nframe = 100

100

In [48]:
seed = MersenneTwister(334)
extracted_qs = sample(seed, 1:576, 50, replace=false);

In [49]:
extracted_qs[1]

240

In [50]:
function logsumexp(x)
    max_x = maximum(x)
    exp_x = exp.(x .- max_x)
    return log(sum(exp_x)) .+ max_x
end

logsumexp (generic function with 1 method)

In [51]:
xs = []
iq_true = extracted_qs[1]
iframe = 1

for r in pred_radii
    @load "data/result/test_radius_$(test_radius)/pred_radius_$(r)/sharpness_$(sharpness)/q_$(nq)/iq_$(iq_true)_noise_$(sigma_noise)_nframe_$(nframe).bson" params r
    #id = argmax(r.all[iframe])
    x = dropdims(r.all[iframe], dims=3)
    #x .= exp.(x)
    #x .= x ./ sum(x)
    x .= x .- logsumexp(x)
    @show sum(exp.(x))
    push!(xs, x)
end

sum(exp.(x)) = 1.0
sum(exp.(x)) = 1.0
sum(exp.(x)) = 1.0
sum(exp.(x)) = 1.0
sum(exp.(x)) = 1.0
sum(exp.(x)) = 1.0
sum(exp.(x)) = 1.0


In [59]:
ps = [];

for i in 1:length(pred_radii)
    likelihood = []
    diff_q = []
    for iq = 1:nq
        for imodel = 1:size(xs[1], 1)
            #push!(diff_q, acos(2.0 * sum(  qs[iq, :] .* qs[iq_true, :] )^2 - 1.0))
            push!(diff_q, quate_dist(qs[iq, :], qs[iq_true, :]))
            push!(likelihood, xs[i][imodel, iq])
        end
    end
    p = scatter(likelihood, diff_q, 
        label=nothing, framestyle=:box,
        xlabel="log likelihood", ylabel="quaternion distance\nfrom the ground-truth",
        markersize=4, markerstrokewidth=0,
        size=(600, 400), dpi=300,
        left_margin=Plots.Measures.Length(:mm, 10.0),
        right_margin=Plots.Measures.Length(:mm, 10.0),
        bottom_margin=Plots.Measures.Length(:mm, 10.0))
    push!(ps, p)
end

In [60]:
plot(ps[4])

In [61]:
for i in 1:length(ps)
    savefig(ps[i], "fig04_$(pred_radii[i])A.png")
end